# TS SCI Classification Model 

## edited: 9 Aug 23

## author: Angus Ferrell

### 1. Initiliaze functions

In [1]:
# Load general utilities
# ----------------------
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.axes as ax
import datetime
import numpy as np
import pickle
import time
import seaborn as sns
import statistics as stat
import random
import glob
import os
import re

# Load sklearn utilities
# ----------------------
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report, roc_auc_score, roc_curve, brier_score_loss, mean_squared_error, r2_score, recall_score, precision_score,f1_score
from sklearn.calibration import calibration_curve
from sklearn.preprocessing import StandardScaler
from statsmodels.stats.outliers_influence import variance_inflation_factor
from sklearn.decomposition import PCA
from sklearn.model_selection import GridSearchCV, StratifiedKFold
from sklearn.metrics import classification_report

# Load classifiers
# ----------------
from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import RidgeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.ensemble import GradientBoostingClassifier
from catboost import CatBoostClassifier

# Other Packages
# --------------
from scipy.stats import kendalltau
from sklearn.cluster import KMeans
from io import StringIO
from IPython.display import Image  
from sklearn.tree import export_graphviz
from scipy.interpolate import BSpline
import matplotlib.pyplot as plt
%matplotlib inline

# Load debugger, if required
pd.options.mode.chained_assignment = None #'warn'

# suppress all warnings
import warnings
warnings.filterwarnings("ignore")

#set random_state
random_state=42

In [2]:
# Check Job Title
# Imported from TECH VIP file

file_name = 'TECH VIP results.csv'
column_to_filter = 'title_1'

def check_jobtitle(data):
    #data = pd.read_csv(file_name, engine = 'python', error_bad_lines = False)
    
    pos = pd.read_csv('TECH VIP/positive ts.csv').dropna(subset=['Keyword'])
    neg = pd.read_csv('TECH VIP/negative.csv').dropna(subset=['Keyword'])

    pos_keys = pos.get('Keyword').tolist()
    pos_keys = [item.lower().strip() for item in pos_keys]


    neg_keys = neg.get('Keyword').tolist()
    neg_keys = [item.lower().strip() for item in neg_keys]


    it_keys = ['izzt ', ' izzt', ' izzt '] #Get IT titles
    
    pos_keys.append('izzt ')
    pos_keys.append(' izzt')
    pos_keys.append(' izzt ')

    pos_keys.append('cto ')
    pos_keys.append(' cto')
    pos_keys.append(' cto ')

    pp = "|".join(pos_keys)
    nn = "|".join(neg_keys)
    
    df = data
    specified_column_1 = column_to_filter #CHANGE SPECIFIED COLUMN HEADER FOR FILTER
    df[specified_column_1] = df[specified_column_1].fillna('')
    
    pos_index = []
    neg_index = []

    for col in df[specified_column_1].items():
        pattern = re.compile(pp)
        stri = col[1].lower()
        find_pat = pattern.findall(stri,0,len(stri))
        if len(find_pat) >= 1:
            pos_index.append(col[0])

    data['job_index'] = 0  # Create a new column 'job_index' initialized with 0
    data.loc[pos_index, 'job_index'] = 1 
    
    for col in df[specified_column_1].items():
        pattern = re.compile(nn)
        stri = col[1].lower()
        find_pat = pattern.findall(stri,0,len(stri))
        if len(find_pat) >= 1:
            neg_index.append(col[0])
            
    data.loc[neg_index, 'job_index'] = -1 
    
    print('Job title - number of pos matches: ', len(pos_index))
    
  

In [3]:
# Check company

company_list = ['General Dynamics Information Technology', 'Gridiron IT Solutions', 'SAIC', 'SPA', 
                'Institute For Defense Analyses', 'IC-CAP', 'Peraton', 'ManTech', 'Tyto Athene LLC',
                'Boeing Intelligence & Analytics', 'Arcfield', 'Leidos', 'Raytheon Technologies', 'CACI', 
                'Booz Allen Hamilton', 'Lockheed Martin', 'ALTA IT Services', 'Cyber Defense Technologies', 
                'TekMasters', 'Emerald Technical Solutions', 'Modern Technology Solutions Inc.', 'VTG', 
                'MITRE Corporation', 'SRG Government Services', 'ManTech International', 'MAXAR Technologies',
                'Leidos', 'Parsons', 'BAE Systems', 'Marathon TS Inc', 'Guidehouse', 'SilverEdge', 'MC Dean Inc', 
                'Trevity LLC', 'teKnoluxion Consulting', 'Northrop Grumman', 'Sentar Inc', 'Stellar Solutions', 
                'Criterion Systems Inc', 'IntelliGenesis LLC', 'LMI Government Consulting', 'MAG Aero', 
                'HII Mission Technologies', 'Enlighten', 'In Technology Group Limited', 'ProSync Technology Group',
                'Connsci', 'Signature Federal Systems', 'Apex Systems', 'Buchanan and Edwards',
                'Radiance Technologies', 'Noblis', 'SRG Government Services', 'Xcelerate Solutions', 
                'DCS Corporation', 'Associates Systems LLC', 'BlueHalo', 'Strategic Alliance Consulting Inc',
                'IT Concepts Inc', 'Barbaricum', 'Forcepoint', 'Federal IT Consulting', 'Canvas Inc', 
                'TEKsystems c/o Allegis Group', 'iota IT', 'Illuminate Operations Inc', 'Compass Inc', 
                'Applied Research Solutions', 'Avineon Inc', 'I3 LLC', 'Assured Information Security Inc',
                'hyrUP', 'Millennium Corporation', 'Core One', 'TekSynap', 'Base-2 Solutions LLC', 'AERMOR', 
                'Amentum', 'Cornerstone Defense', 'Base One Technologies', 'ALTA IT Services', 'Sentar Inc', 
                'Ennoble First', 'Core4ce', 'Syntelligent Analytic Solutions LLC', 'Serco Inc', 
                'Space Dynamics Laboratory', 'RDR Inc', 'MicroTech LLC', 'North Point Technology LLC', 
                'LinQuest Corporation', 'Kavaliro', 'SOSi', 'Allen Integrated Solutions LLC',
                'Columbia Technology Partners', 'Dark Wolf Solutions', 'Strategic Alliance Consulting Inc',
                'MAXAR Technologies', 'AT&T Government Solutions', 'Invictus International Consulting', 
                'Secure Halo', 'Octo', 'Lumen', 'Applied Insight', 'PeopleTec', 'NASK', 'Highlight Technologies',
                'JCTM Joint Computer Technologies & Training Management', 'ClearEdge IT Solutions LLC',
                'Echelon Services LLC', 'Clear Resolution Consulting LLC', 'American Systems Corporation', 
                'Abile Group', 'KBR', 'Abbtech Professional Resources Inc', 'Stanley Reid & Company', 
                'Stillwater Human Capital', 'Fluor Corporation', 'Chenega Corporation', 'RMGS Inc', 
                'Moseley Technical Services Inc', 'Personnel Impact Inc', 'Rividium Inc', 'Edgesource',
                'Sunayu LLC', 'SSATI', 'Distributed Solutions Inc', 'Information Gateways Inc', 'ENSCO Inc',
                'Independent Software', 'Avantus Federal', 'Strategic ASI', 'IOMAXIS LLC', 
                'StraCon Services Group LLC', 'Railhead Inc', 'CONNEXIONS FEDERAL SERVICES', 
                'Valiant Integrated Services', 'Intelligent Waves', 'Maximus Inc', 'Thresher Corporation',
                'Market Street Talent', 'Odyssey Systems Consulting Group', 'Quantum Research International Inc',
                'Dezign-Concepts', 'The DarkStar Group', 'Red River Technology LLC', 'Mission Box Solutions',
                'Executive Management Services LLC', 'The Global Edge Consultants', 'TRIAEM LLC',
                'Delta Solutions and Strategies LLC', 'Intrepid Solutions and Services LLC', 'FiveTwelve LLC',
                'CACI International Inc', 'Raytheon', 'Deloitte','Oshkosh', 'Boeing','Accenture Federal Services',
                'Palantir Technologies','US Army','US Navy','United States Air Force','Department of Defense','USAF']




military_pattern = r'US Army|US Navy|air force|usaf|marines|special operations|special forces| socom |Department of Defense| DoD '

#gov_pattern = r'Central Intelligence Agency|CIA|National Security Agency|NSA|Federal Bureau of Investigation|FBI|Department of State|Department of Homeland Security|DHS|Defense Intelligence Agency|DIA|National Reconnaissance Office|NRO|National Geospatial-Intelligence Agency|NGA|United States Secret Service|Drug Enforcement Administration|DEA|National Counterterrorism Center|NCTC|Bureau of Alcohol, Tobacco, Firearms, and Explosives|ATF|Department of Energy|DOE|Department of Justice|DOJ'
                    # FBI | NSA | DOJ | CIA | DHS | DIA 


def check_company(df):

    # Fill missing values with an empty string
    df['company_1'] = df['company_1'].fillna('NaN')
    df['company_2'] = df['company_2'].fillna('NaN')
    df['company_1'] = df['company_1'].replace('U.S. Navy', 'US Navy')
    df['company_2'] = df['company_2'].replace('U.S. Navy', 'US Navy')
    df['company_1'] = df['company_1'].replace('U.S. Army', 'US Army')
    df['company_2'] = df['company_2'].replace('U.S. Army', 'US Army')
    df['company_1'] = df['company_1'].replace('CACI', 'CACI International Inc')
    df['company_2'] = df['company_2'].replace('CACI', 'CACI International Inc')
    df['company_1'] = df['company_1'].replace('Raytheon', 'Raytheon Technologies')
    df['company_2'] = df['company_2'].replace('Raytheon', 'Raytheon Technologies')
    df['company_1'] = df['company_1'].replace('Northrop Grumman Corporation', 'Northrop Grumman')
    df['company_2'] = df['company_2'].replace('Northrop Grumman Corporation', 'Northrop Grumman')
    df['company_1'] = df['company_1'].replace('Palantir', 'Palantir Technologies')
    df['company_2'] = df['company_2'].replace('Palantir', 'Palantir Technologies')
    df['company_1'] = df['company_1'].replace('BAE Systems, Inc.', 'BAE Systems')
    
    
    #Apply regex pattern to filter DataFrame
    df['company_index'] = df.apply(lambda row: int(1) if row['company_1'] in company_list or 
                                   re.search(military_pattern, row['company_1'], re.IGNORECASE) 
                                   else int(0), axis=1)
    
    #df['company_index'] = df.apply(calculate_company_index, axis=1)
    print('Company - Number of matches: ', np.sum(df.company_index==1))

In [4]:
# Check skills

# Regex pattern
skills_pattern = r'TS CLEARANCE|TS/SCI|TOP SECRET CLEARANCE|ACTIVE TS CLEARANCE| TS SCI |TS SCI CLEARANCE|POLYGRAPGH| CI POLY|FULL SCOPE POLY'

def check_skills(df):

    # Fill missing values with an empty string
    df['Skills'] = df['Skills'].fillna('')
    
     # Apply regex pattern to filter DataFrame
    df['skills_index'] = df.apply(lambda row: 1 if re.search(skills_pattern, row['Skills'], 
                                                             re.IGNORECASE) else 0, axis=1)

    print('Skills - Number of matches: ', np.sum(df.skills_index==1))

In [5]:
# Check summary

def check_summary(df):
    
    # Fill missing values with an empty string
    df['Summary'] = df['Summary'].fillna('')

    # Apply regex pattern to filter DataFrame
    df['summary_index'] = df.apply(lambda row: 1 if re.search(skills_pattern, row['Summary'], 
                                                              re.IGNORECASE) else 0, axis=1)

    print('Summary - Number of matches: ', np.sum(df.summary_index==1))
    
    

In [6]:
# Check job description


def check_desc(df):
    
    # Fill missing values with an empty string
    df['Job_Description_1'] = df['Job_Description_1'].fillna('')
    #df['Job_Description_2'] = df['Job_Description_2'].fillna('')

    # Apply regex pattern to filter DataFrame
    df['desc_index'] = df.apply(lambda row: 1 if re.search(skills_pattern, row['Job_Description_1'], 
                                                              re.IGNORECASE) else 0, axis=1)

    print('Description - Number of matches: ', np.sum(df.desc_index==1))
    
    

In [7]:
# Check location based on states with highest liklihood of TS 

popular_states = ['Virginia','Maryland','California','District of Columbia','Florida','Colorado','Utah','Texas',
                 'Alabama','New Mexico','Ohio','Georgia','Hawaii', 'North Carolina','South Carolina', 'Arizona',
                  'Washington']


def check_location(df):
    
     # Fill missing values with an empty string
    df['State'] = df['State'].fillna('')

    # Apply regex pattern to filter DataFrame
    df['location_index'] = df.apply(lambda row: 1 if row['State'] in popular_states else 0, axis=1)
    
   
    print('Location - Number of matches: ', np.sum(df.location_index==1))

    

In [8]:
# Check names
# using 2000 most common US census data names

common_names = pd.read_csv('common_names.csv').dropna(subset=['Keyword'])

name_list = []

for name in common_names.Keyword:
    name_list.append(name)


def check_name(df):
    
     # Fill missing values with an empty string
    df['First Name'] = df['First Name'].fillna('')

    # Apply regex pattern to filter DataFrame
    df['name_index'] = df.apply(lambda row: 1 if row['First Name'].upper() in name_list else 0, axis=1)
    
   
    print('Names - Number of matches: ', np.sum(df.name_index==1))

In [9]:
#this code creates an equal number of positive and random cases from the imported dataset
#then creates the respective class labels
#returns a training data dataframe and labels array

def create_trainingdata(data,random_state = random_state):
    
    columns = ['Linkedin_url','Summary', 'Skills', 'title_1',
       'company_1', 'time_duration_1', 'Job_Description_1', 'title_2',
       'company_2', 'time_duration_2', 'Job_Description_2', 
       'First Name','Middle Name', 'Surname', 'City', 'State', 'Country']
    
    training_data = check_for_keywords(data)
    training_data = training_data[columns]
    
    val_labels = np.ones(len(training_data))

    num_numbers = len(training_data)
    min_num = 1
    max_num = len(data)

    training_data_indices = training_data.index
    
    random_generator = random.Random(random_state)

    
    ### create training data at 9:1 ratio
    ### sample from full dataset

    random_numbers = []
    target_length = 9 * num_numbers
        
    while len(random_numbers) < target_length and len(random_numbers) < len(data):
        random_num = random_generator.randint(min_num, max_num)
        if random_num in data.index:
            random_numbers.append(random_num)      
        

    random_data_df = data.loc[random_numbers, columns]
    random_data_indices = random_data_df.index

    random_labels = np.zeros(len(random_numbers))

    training_data_df = pd.concat([training_data, random_data_df])
    training_data_labels = np.append(val_labels, random_labels)

    x_unlabeled_indices = data.index.difference(training_data_indices.union(random_data_indices))
    x_unlabeled_df = data.loc[x_unlabeled_indices, columns]

    return training_data_df, training_data_labels, x_unlabeled_df


In [10]:

def check_for_keywords(df):
    
    keywords = ['TS CLEARANCE','TS/SCI','TOP SECRET CLEARANCE','ACTIVE TS CLEARANCE', 'TS SCI','TS SCI CLEARANCE','POLYGRAPH','CI POLY','FULL SCOPE POLY']
    keyword_rows = []

    for index, row in df.iterrows():
        for column in df.columns:
            cell_value = str(row[column]).upper()
            if any(keyword in cell_value for keyword in keywords):
                keyword_rows.append(index)
                break  # Move to the next row if keyword found in any column

    print('# matches: ',len(keyword_rows))   
    
    output = df.iloc[keyword_rows]
    
    return output



In [11]:
# Define a function that, given a CVGridSearch object, finds the
# percentage difference between the best and worst scores

def find_score_variation(cv_model):
    all_scores = cv_model.cv_results_['mean_test_score']
    return( np.abs((max(all_scores) - min(all_scores))) * 100 / max(all_scores) )


# Define a function that checks, given a CVGridSearch object,
# whether the optimal parameters lie on the edge of the search
# grid
def find_opt_params_on_edge(cv_model):
    out = False
    
    for i in cv_model.param_grid:
        if cv_model.best_params_[i] in [ cv_model.param_grid[i][0], cv_model.param_grid[i][-1] ]:
            out = True
            break
            
    return out


default_seed = 0
output_file = "output_sample"

# Create a function to print a line to our output file

def dump_to_output(key, value):
    with open(output_file, "a") as f:
        f.write(",".join([str(default_seed), key, str(value)]) + "\n")

In [12]:
def fit_classification(model, X_train,y_train, X_test, y_test,
                          cv_parameters = {},
                          model_name = None,
                          random_state = random_state,
                          output_to_file = True,
                          print_to_screen = True):
    
    np.random.seed(random_state)

    # --------------------------
    #   Step 2 - Fit the model
    # --------------------------

    cv_model = GridSearchCV(model, cv_parameters)
    
    start_time = time.time()
    cv_model.fit(X_train, y_train,cat_features=categorical_features_indices)
    end_time = time.time()
    
    best_model = cv_model.best_estimator_
    
    if print_to_screen:

        if model_name != None:
            print("=========================================================")
            print("  Model: " + model_name)
            print("=========================================================")

        print("Fit time: " + str(round(end_time - start_time, 2)) + " seconds")
        print("Optimal parameters:")
        print(cv_model.best_params_)
        print("")
    
    # -------------------------------
    #   Step 3 - Evaluate the model
    # -------------------------------
    
    # If possible, make probability predictions
    try:
        y_pred_probs = best_model.predict_proba(X_test)[:,1]
        fpr, tpr, thresholds = roc_curve(y_test, y_pred_probs)
        
        probs_predicted = True
    except:
        probs_predicted = False
    
    # Make predictions; if we were able to find probabilities, use
    # the threshold that maximizes the accuracy in the training set.
    # If not, just use the learner's predict function
    if probs_predicted:
        y_train_pred_probs = best_model.predict_proba(X_train)[:,1]
        fpr_train, tpr_train, thresholds_train = roc_curve(y_train, y_train_pred_probs)
        
        true_pos_train = tpr_train*(y_train.sum())
        true_neg_train = (1 - fpr_train) *(1-y_train).sum()
        
        best_threshold_index = np.argmax(true_pos_train + true_neg_train)
        best_threshold = 1 if best_threshold_index == 0 else thresholds_train[ best_threshold_index ]
        
        if print_to_screen:
            print("Accuracy-maximizing threshold was: " + str(best_threshold))
        
        y_pred = (y_pred_probs > best_threshold)
    else:
        y_pred = best_model.predict(X_test)
    
    if print_to_screen:
        print("Accuracy: ", accuracy_score(y_test, y_pred))
        print(classification_report(y_test, y_pred, target_names =['No TS', 'TS'], digits = 4))

    if print_to_screen:
        if probs_predicted:        
            plt.figure(figsize = (13, 4.5))
            plt.subplot(2, 2, 1)

            plt.title("ROC Curve (AUC = %0.2f)"% roc_auc_score(y_test, y_pred_probs))
            plt.plot(fpr, tpr, 'b')
            plt.plot([0,1],[0,1],'r--')
            plt.xlim([0,1]); plt.ylim([0,1])
            plt.ylabel('True Positive Rate')
            plt.xlabel('False Positive Rate')

            plt.subplot(2, 2, 3)

            plt.plot(thresholds, tpr, 'b', label = 'Sensitivity')
            plt.plot(thresholds, 1 -fpr, 'r', label = 'Specificity')
            plt.legend(loc = 'lower right')
            plt.xlim([0,1]); plt.ylim([0,1])
            plt.xlabel('Threshold')

            plt.subplot(2, 2, 2)

            fp_0, mpv_0 = calibration_curve(y_test, y_pred_probs, n_bins = 10)
            plt.plot([0,1], [0,1], 'k:', label='Perfectly calibrated')
            plt.plot(mpv_0, fp_0, 's-')
            plt.ylabel('Fraction of Positives')
            plt.xlim([0,1]); plt.ylim([0,1])
            plt.legend(loc ='upper left')
            
            plt.subplot(2, 2, 4)
            plt.hist(y_pred_probs, range=(0, 1), bins=10, histtype="step", lw=2)
            plt.xlim([0,1]); plt.ylim([0,20000])
            plt.xlabel('Mean Predicted Probability')
            plt.ylabel('Count')
            
            #plt.tight_layout()
            plt.show()
        
    # Additional Score Check
    if probs_predicted:
        y_train_score = y_train_pred_probs
    else:
        y_train_score = best_model.decision_function(X_train)
        
    
    if probs_predicted:
        brier_score = brier_score_loss(y_test, y_pred_probs)
        if print_to_screen:
            print("Brier score:", brier_score)
    
    # Return the model predictions, and the
    # test set
    # -------------------------------------
    out = {'model':best_model, 'y_pred_labels':y_pred}
    
    if probs_predicted:
        out.update({'y_pred_probs':y_pred_probs})
    else:
        y_pred_score = best_model.decision_function(X_test)
        out.update({'y_pred_score':y_pred_score})
 
    return out


In [13]:
def test_model(best_model, X_train,y_train, X_test, y_test, print_to_screen = True):
    try:
        y_pred_probs = best_model.predict_proba(X_test)[:,1]
        fpr, tpr, thresholds = roc_curve(y_test, y_pred_probs)
        
        probs_predicted = True
    except:
        probs_predicted = False
    
    # Make predictions; if we were able to find probabilities, use
    # the threshold that maximizes the accuracy in the training set.
    # If not, just use the learner's predict function
    if probs_predicted:
        y_train_pred_probs = best_model.predict_proba(X_train)[:,1]
        fpr_train, tpr_train, thresholds_train = roc_curve(y_train, y_train_pred_probs)
        
        true_pos_train = tpr_train*(y_train.sum())
        true_neg_train = (1 - fpr_train) *(1-y_train).sum()
        
        best_threshold_index = np.argmax(true_pos_train + true_neg_train)
        best_threshold = 1 if best_threshold_index == 0 else thresholds_train[ best_threshold_index ]
        
        if print_to_screen:
            print("Accuracy-maximizing threshold was: " + str(best_threshold))
        
        y_pred = (y_pred_probs > best_threshold)
    else:
        y_pred = best_model.predict(X_test)
    
    if print_to_screen:
        print("Accuracy: ", accuracy_score(y_test, y_pred))
        print(classification_report(y_test, y_pred, target_names =['No TS', 'TS'], digits = 4))

    if print_to_screen:
        if probs_predicted:        
            plt.figure(figsize = (13, 4.5))
            plt.subplot(2, 2, 1)

            plt.title("ROC Curve (AUC = %0.2f)"% roc_auc_score(y_test, y_pred_probs))
            plt.plot(fpr, tpr, 'b')
            plt.plot([0,1],[0,1],'r--')
            plt.xlim([0,1]); plt.ylim([0,1])
            plt.ylabel('True Positive Rate')
            plt.xlabel('False Positive Rate')

            plt.subplot(2, 2, 3)

            plt.plot(thresholds, tpr, 'b', label = 'Sensitivity')
            plt.plot(thresholds, 1 -fpr, 'r', label = 'Specificity')
            plt.legend(loc = 'lower right')
            plt.xlim([0,1]); plt.ylim([0,1])
            plt.xlabel('Threshold')

            plt.subplot(2, 2, 2)

            fp_0, mpv_0 = calibration_curve(y_test, y_pred_probs, n_bins = 10)
            plt.plot([0,1], [0,1], 'k:', label='Perfectly calibrated')
            plt.plot(mpv_0, fp_0, 's-')
            plt.ylabel('Fraction of Positives')
            plt.xlim([0,1]); plt.ylim([0,1])
            plt.legend(loc ='upper left')
            
            plt.subplot(2, 2, 4)
            plt.hist(y_pred_probs, range=(0, 1), bins=10, histtype="step", lw=2)
            plt.xlim([0,1]); plt.ylim([0,20000])
            plt.xlabel('Mean Predicted Probability')
            plt.ylabel('Count')
            
            #plt.tight_layout()
            plt.show()
        
    # Additional Score Check
    if probs_predicted:
        y_train_score = y_train_pred_probs
    else:
        y_train_score = best_model.decision_function(X_train)
    
    if probs_predicted:
        brier_score = brier_score_loss(y_test, y_pred_probs)
        if print_to_screen:
            print("Brier score:", brier_score)


### 2. Build Training Dataset

In [14]:
training_files = glob.glob('updated_datasets/*.csv')
print(training_files)

['updated_datasets/updated_lifull_12.2022.csv', 'updated_datasets/updated_lifull_419M3.csv', 'updated_datasets/updated_lifull_419_M2.csv', 'updated_datasets/updated_more_training_data.csv', 'updated_datasets/updated_lifull_419M1.csv', 'updated_datasets/updated_lifull_bing2_212.csv', 'updated_datasets/updated_lifull_322_0.csv', 'updated_datasets/updated_li_full_11_22.csv', 'updated_datasets/updated_lifull_303.csv', 'updated_datasets/updated_lifull_326-001.csv', 'updated_datasets/updated_lifull_bing1_212.csv', 'updated_datasets/updated_lifull_326-000.csv', 'updated_datasets/updated_lifull_326-002.csv', 'updated_datasets/updated_lifull_reg_212.csv', 'updated_datasets/updated_lifull_1_2023.csv', 'updated_datasets/updated_lifull_309_1.csv', 'updated_datasets/updated_lifull_309_2_3.csv']


In [15]:
training_df = []
labels = []
unlabeled_list = []

for filename in training_files:
    
    # Call create_trainingdata function
    data = pd.read_csv(filename) 
    df, label, unlabeled = create_trainingdata(data,random_state)
    
    # Append dataframe and label to respective lists
    training_df.append(df)
    labels.append(label)
    unlabeled_list.append(unlabeled)
 
print('number of training sets: ',len(training_df))

# matches:  399
# matches:  508
# matches:  703
# matches:  4106
# matches:  616
# matches:  373
# matches:  358
# matches:  386
# matches:  481
# matches:  398
# matches:  361
# matches:  393
# matches:  326
# matches:  260
# matches:  601
# matches:  333
# matches:  473
number of training sets:  17


In [16]:
### Combine all training data ###

training_data_new = pd.concat(training_df)

training_data_new.fillna({'connections':0, 'company_1':'NaN', 'company_2':'NaN',
                    'company_3':'NaN', 'company_4':'NaN', 'Summary':'','Skills':'','Job_Description_1':'',
                    'First Name':'','Surname':'','State':'','title_1':'',
                    'title_2':'', 'Surname':'', 'City':'', 'Country':''}, inplace=True)

print('training data: ', training_data_new.shape)

training_labels_new = np.concatenate(labels)
print('training data labels: ', training_labels_new.shape)

X_unlabeled_raw = pd.concat(unlabeled_list)
print('unlabeled data: ', X_unlabeled_raw.shape)

training data:  (110750, 17)
training data labels:  (110750,)
unlabeled data:  (3069121, 17)


In [17]:
#Remove invalid labels 

training_labels_new[training_data_new['company_1']=='NaN'] = 0
training_labels_new[training_data_new['company_1']=='Retired'] = 0
training_labels_new[training_data_new['company_1']=='Self-employed'] = 0
training_labels_new[training_data_new['company_1']=='USAA'] = 0
training_labels_new[training_data_new['company_1']=='Wells Fargo'] = 0

countries = ['United States']
training_labels_new[~training_data_new['Country'].isin(countries)] = 0

keywords = ['fitness','gym', 'health', 'therapeutic','finance']
mask = training_data_new['company_1'].str.lower().str.contains('|'.join(keywords))
training_labels_new[mask] = 0

In [18]:
#Write out training data
'''
check_jobtitle(training_data_new)
check_company(training_data_new)
check_location(training_data_new)
check_skills(training_data_new)
check_summary(training_data_new)
check_desc(training_data_new)

df_out = training_data_new
df_out['Label'] = training_labels_new
df_out.to_csv('training data 24 July.csv', index=False)

#write out all data
training_files = glob.glob('datasets/*.csv')

       
#filename_out = 'Combined__datasets.csv'
#combined_data = pd.concat(files, ignore_index=True)
#combined_data.to_csv(filename_out, index=False)
'''

"\ncheck_jobtitle(training_data_new)\ncheck_company(training_data_new)\ncheck_location(training_data_new)\ncheck_skills(training_data_new)\ncheck_summary(training_data_new)\ncheck_desc(training_data_new)\n\ndf_out = training_data_new\ndf_out['Label'] = training_labels_new\ndf_out.to_csv('training data 24 July.csv', index=False)\n\n#write out all data\ntraining_files = glob.glob('datasets/*.csv')\n\n       \n#filename_out = 'Combined__datasets.csv'\n#combined_data = pd.concat(files, ignore_index=True)\n#combined_data.to_csv(filename_out, index=False)\n"

In [19]:
### Random Sample ###

'''
training_files = glob.glob('datasets/*.csv')

files = []
for filename in training_files:
    data = pd.read_csv(filename)
    files.append(data)
    
#output = np.concatenate(files, axis=1)
output = pd.concat(files, ignore_index=True)


#sample_data = sample.sample(n=100000, random_state=42)  # Setting random_state for reproducibility

# Write the sampled data to 'data_sample.csv'
#sample_data.to_csv('data_sample.csv', index=False)

#print("Random sample of 100,000 rows has been written to 'data_sample.csv'.")
'''

'\ntraining_files = glob.glob(\'datasets/*.csv\')\n\nfiles = []\nfor filename in training_files:\n    data = pd.read_csv(filename)\n    files.append(data)\n    \n#output = np.concatenate(files, axis=1)\noutput = pd.concat(files, ignore_index=True)\n\n\n#sample_data = sample.sample(n=100000, random_state=42)  # Setting random_state for reproducibility\n\n# Write the sampled data to \'data_sample.csv\'\n#sample_data.to_csv(\'data_sample.csv\', index=False)\n\n#print("Random sample of 100,000 rows has been written to \'data_sample.csv\'.")\n'

### 3. Train CatBoost Model

In [20]:
### Catboost Training Data ###

check_jobtitle(training_data_new)
check_company(training_data_new)
check_location(training_data_new)
check_skills(training_data_new)
check_summary(training_data_new)
check_desc(training_data_new)
#check_name(training_data_new)

catboost_columns = ['job_index', 'skills_index','summary_index','location_index','company_index'
                    ,'desc_index', 'title_1', 'company_1','State','Country']

training_data_final2 = training_data_new[catboost_columns]


X_train, X_test, y_train, y_test = train_test_split(training_data_final2, training_labels_new, test_size=0.10, 
                                                    random_state=random_state, stratify=training_labels_new)


from imblearn.under_sampling import RandomUnderSampler

# Undersample the majority class (target 0)
rus = RandomUnderSampler(sampling_strategy=0.75, random_state=random_state)
X_train, y_train = rus.fit_resample(X_train, y_train)


print(X_train.shape)
print(y_train.shape)
print(X_test.shape)
print(y_test.shape)

categorical_features_indices = np.where(X_train.dtypes != int)[0]
categorical_features_indices
y_train = pd.to_numeric(y_train).astype('int32')
y_test = pd.to_numeric(y_test).astype('int32')

Job title - number of pos matches:  2138
Company - Number of matches:  5211
Location - Number of matches:  61369
Skills - Number of matches:  181
Summary - Number of matches:  6590
Description - Number of matches:  392
(21753, 10)
(21753,)
(11075, 10)
(11075,)


In [21]:
train_pos = np.sum(y_train==1)
tot = len(y_train)
print('train set TS ratio',train_pos/tot)

test_pos = np.sum(y_test==1)
tot = len(y_test)
print('test set TS ratio',test_pos/tot)

train set TS ratio 0.4285845630487749
test set TS ratio 0.09354401805869074


In [22]:
#clean unlabeled data

check_jobtitle(X_unlabeled_raw)
check_company(X_unlabeled_raw)
check_location(X_unlabeled_raw)
check_skills(X_unlabeled_raw)
check_summary(X_unlabeled_raw)
check_desc(X_unlabeled_raw)

X_unlabeled_raw.fillna({'connections':0, 'company_1':'NaN', 'company_2':'NaN',
                    'company_3':'NaN', 'company_4':'NaN', 'Summary':'','Skills':'','Job_Description_1':'',
                    'First Name':'','Surname':'','State':'','title_1':'',
                    'title_2':'', 'Surname':'', 'City':'', 'Country':''}, inplace=True)

X_unlabeled = X_unlabeled_raw[catboost_columns]

Job title - number of pos matches:  43978
Company - Number of matches:  78688
Location - Number of matches:  1640405
Skills - Number of matches:  0
Summary - Number of matches:  0
Description - Number of matches:  0


In [23]:
### Find best hyperparamters ###

CatBoost = CatBoostClassifier(iterations=100,random_seed=random_state)

cv_parameters = {
    'learning_rate': [0.01,0.1,0.3],
    'depth': [4,10,12],
    'l2_leaf_reg':[4, 10,12],
    'random_strength':[0,10],
    'class_weights': [[1,1],[1,1.25],[1,1.5]],
    'eval_metric': ['Recall','Precision'],
    'custom_loss': ['Recall','Precision']}

cb = fit_classification(CatBoost, X_train,y_train, X_test, y_test, cv_parameters,
                         'CatBoost', output_to_file = False)

0:	learn: 0.7038080	total: 105ms	remaining: 10.4s
1:	learn: 0.7038080	total: 112ms	remaining: 5.51s
2:	learn: 0.7038080	total: 126ms	remaining: 4.08s
3:	learn: 0.7038080	total: 130ms	remaining: 3.12s
4:	learn: 0.7038080	total: 137ms	remaining: 2.59s
5:	learn: 0.7038080	total: 145ms	remaining: 2.27s
6:	learn: 0.7038080	total: 151ms	remaining: 2.01s
7:	learn: 0.7038080	total: 159ms	remaining: 1.82s
8:	learn: 0.7038080	total: 166ms	remaining: 1.68s
9:	learn: 0.7038080	total: 181ms	remaining: 1.63s
10:	learn: 0.7038080	total: 185ms	remaining: 1.5s
11:	learn: 0.7038080	total: 189ms	remaining: 1.39s
12:	learn: 0.7038080	total: 205ms	remaining: 1.37s
13:	learn: 0.7038080	total: 209ms	remaining: 1.28s
14:	learn: 0.7038080	total: 225ms	remaining: 1.27s
15:	learn: 0.7047466	total: 229ms	remaining: 1.2s
16:	learn: 0.7074283	total: 233ms	remaining: 1.14s
17:	learn: 0.7074283	total: 237ms	remaining: 1.08s
18:	learn: 0.7076964	total: 241ms	remaining: 1.03s
19:	learn: 0.7138643	total: 252ms	remaining

85:	learn: 0.6183964	total: 478ms	remaining: 77.8ms
86:	learn: 0.6183964	total: 482ms	remaining: 72.1ms
87:	learn: 0.6209440	total: 492ms	remaining: 67ms
88:	learn: 0.6209440	total: 496ms	remaining: 61.3ms
89:	learn: 0.6209440	total: 500ms	remaining: 55.6ms
90:	learn: 0.6209440	total: 506ms	remaining: 50.1ms
91:	learn: 0.6209440	total: 510ms	remaining: 44.4ms
92:	learn: 0.6209440	total: 515ms	remaining: 38.8ms
93:	learn: 0.6209440	total: 521ms	remaining: 33.2ms
94:	learn: 0.6183964	total: 524ms	remaining: 27.6ms
95:	learn: 0.6190668	total: 531ms	remaining: 22.1ms
96:	learn: 0.6192009	total: 538ms	remaining: 16.6ms
97:	learn: 0.6190668	total: 543ms	remaining: 11.1ms
98:	learn: 0.6205417	total: 547ms	remaining: 5.52ms
99:	learn: 0.6192009	total: 551ms	remaining: 0us
0:	learn: 0.6065969	total: 17.4ms	remaining: 1.72s
1:	learn: 0.6065969	total: 53.3ms	remaining: 2.61s
2:	learn: 0.6065969	total: 71.3ms	remaining: 2.3s
3:	learn: 0.6065969	total: 89.2ms	remaining: 2.14s
4:	learn: 0.6163851	to

64:	learn: 0.6315860	total: 512ms	remaining: 276ms
65:	learn: 0.6315860	total: 527ms	remaining: 272ms
66:	learn: 0.6315860	total: 531ms	remaining: 261ms
67:	learn: 0.6315860	total: 536ms	remaining: 252ms
68:	learn: 0.6315860	total: 540ms	remaining: 242ms
69:	learn: 0.6315860	total: 544ms	remaining: 233ms
70:	learn: 0.6315860	total: 548ms	remaining: 224ms
71:	learn: 0.6315860	total: 553ms	remaining: 215ms
72:	learn: 0.6315860	total: 559ms	remaining: 207ms
73:	learn: 0.6315860	total: 571ms	remaining: 201ms
74:	learn: 0.6315860	total: 575ms	remaining: 192ms
75:	learn: 0.6315860	total: 578ms	remaining: 183ms
76:	learn: 0.6315860	total: 582ms	remaining: 174ms
77:	learn: 0.6315860	total: 587ms	remaining: 165ms
78:	learn: 0.6315860	total: 591ms	remaining: 157ms
79:	learn: 0.6315860	total: 594ms	remaining: 149ms
80:	learn: 0.6315860	total: 599ms	remaining: 140ms
81:	learn: 0.6315860	total: 602ms	remaining: 132ms
82:	learn: 0.6315860	total: 606ms	remaining: 124ms
83:	learn: 0.6315860	total: 614

46:	learn: 0.5422365	total: 417ms	remaining: 470ms
47:	learn: 0.5425047	total: 439ms	remaining: 475ms
48:	learn: 0.5429069	total: 447ms	remaining: 466ms
49:	learn: 0.5438455	total: 458ms	remaining: 458ms
50:	learn: 0.5445160	total: 462ms	remaining: 444ms
51:	learn: 0.5454545	total: 469ms	remaining: 433ms
52:	learn: 0.5450523	total: 472ms	remaining: 418ms
53:	learn: 0.5466613	total: 480ms	remaining: 409ms
54:	learn: 0.5470636	total: 490ms	remaining: 401ms
55:	learn: 0.5473317	total: 505ms	remaining: 397ms
56:	learn: 0.5474658	total: 509ms	remaining: 384ms
57:	learn: 0.5477340	total: 522ms	remaining: 378ms
58:	learn: 0.5482703	total: 525ms	remaining: 365ms
59:	learn: 0.5490748	total: 533ms	remaining: 355ms
60:	learn: 0.5506838	total: 541ms	remaining: 346ms
61:	learn: 0.5504157	total: 549ms	remaining: 336ms
62:	learn: 0.5516224	total: 553ms	remaining: 325ms
63:	learn: 0.5517565	total: 557ms	remaining: 313ms
64:	learn: 0.5528292	total: 561ms	remaining: 302ms
65:	learn: 0.5537678	total: 564

31:	learn: 0.5435774	total: 215ms	remaining: 457ms
32:	learn: 0.5430410	total: 223ms	remaining: 454ms
33:	learn: 0.5430410	total: 227ms	remaining: 441ms
34:	learn: 0.5430410	total: 232ms	remaining: 431ms
35:	learn: 0.5431751	total: 238ms	remaining: 424ms
36:	learn: 0.5419684	total: 241ms	remaining: 410ms
37:	learn: 0.5414320	total: 245ms	remaining: 400ms
38:	learn: 0.5411639	total: 249ms	remaining: 389ms
39:	learn: 0.5415661	total: 253ms	remaining: 379ms
40:	learn: 0.5415661	total: 257ms	remaining: 370ms
41:	learn: 0.5434433	total: 272ms	remaining: 376ms
42:	learn: 0.5446500	total: 277ms	remaining: 368ms
43:	learn: 0.5446500	total: 283ms	remaining: 360ms
44:	learn: 0.5442478	total: 287ms	remaining: 351ms
45:	learn: 0.5437115	total: 291ms	remaining: 342ms
46:	learn: 0.5439796	total: 330ms	remaining: 372ms
47:	learn: 0.5434433	total: 333ms	remaining: 361ms
48:	learn: 0.5446500	total: 338ms	remaining: 351ms
49:	learn: 0.5443819	total: 341ms	remaining: 341ms
50:	learn: 0.5439796	total: 345

...

42:	learn: 0.7198981	total: 652ms	remaining: 864ms
43:	learn: 0.7220434	total: 672ms	remaining: 856ms
44:	learn: 0.7235184	total: 686ms	remaining: 838ms
45:	learn: 0.7244570	total: 721ms	remaining: 846ms
46:	learn: 0.7235184	total: 738ms	remaining: 832ms
47:	learn: 0.7257978	total: 756ms	remaining: 819ms
48:	learn: 0.7296862	total: 790ms	remaining: 822ms
49:	learn: 0.7288817	total: 808ms	remaining: 808ms
50:	learn: 0.7294181	total: 832ms	remaining: 799ms
51:	learn: 0.7300885	total: 861ms	remaining: 795ms
52:	learn: 0.7307589	total: 879ms	remaining: 779ms
53:	learn: 0.7303567	total: 900ms	remaining: 766ms
54:	learn: 0.7291499	total: 914ms	remaining: 747ms
55:	learn: 0.7299544	total: 950ms	remaining: 746ms
56:	learn: 0.7314293	total: 963ms	remaining: 727ms
57:	learn: 0.7314293	total: 985ms	remaining: 713ms
58:	learn: 0.7337088	total: 1.01s	remaining: 706ms
59:	learn: 0.7338429	total: 1.04s	remaining: 694ms
60:	learn: 0.7335747	total: 1.05s	remaining: 674ms
61:	learn: 0.7339769	total: 1.0

13:	learn: 0.7228851	total: 329ms	remaining: 2.02s
14:	learn: 0.7224829	total: 336ms	remaining: 1.91s
15:	learn: 0.7235554	total: 351ms	remaining: 1.84s
16:	learn: 0.7266390	total: 356ms	remaining: 1.74s
17:	learn: 0.7261027	total: 367ms	remaining: 1.67s
18:	learn: 0.7293203	total: 385ms	remaining: 1.64s
19:	learn: 0.7318675	total: 391ms	remaining: 1.56s
20:	learn: 0.7326719	total: 397ms	remaining: 1.49s
21:	learn: 0.7321357	total: 431ms	remaining: 1.53s
22:	learn: 0.7336104	total: 463ms	remaining: 1.55s
23:	learn: 0.7341467	total: 588ms	remaining: 1.86s
24:	learn: 0.7341467	total: 591ms	remaining: 1.77s
25:	learn: 0.7337445	total: 604ms	remaining: 1.72s
26:	learn: 0.7337445	total: 606ms	remaining: 1.64s
27:	learn: 0.7341467	total: 626ms	remaining: 1.61s
28:	learn: 0.7332082	total: 631ms	remaining: 1.54s
29:	learn: 0.7356214	total: 655ms	remaining: 1.53s
30:	learn: 0.7358895	total: 665ms	remaining: 1.48s
31:	learn: 0.7361577	total: 675ms	remaining: 1.43s
32:	learn: 0.7361577	total: 679

81:	learn: 0.8907376	total: 2.11s	remaining: 464ms
82:	learn: 0.8907376	total: 2.13s	remaining: 437ms
83:	learn: 0.8907376	total: 2.14s	remaining: 408ms
84:	learn: 0.8907376	total: 2.16s	remaining: 381ms
85:	learn: 0.8907376	total: 2.29s	remaining: 373ms
86:	learn: 0.8907376	total: 2.31s	remaining: 345ms
87:	learn: 0.8907376	total: 2.32s	remaining: 317ms
88:	learn: 0.8907376	total: 2.34s	remaining: 290ms
89:	learn: 0.8907376	total: 2.36s	remaining: 262ms
90:	learn: 0.8907376	total: 2.38s	remaining: 235ms
91:	learn: 0.8907376	total: 2.4s	remaining: 209ms
92:	learn: 0.8907376	total: 2.44s	remaining: 184ms
93:	learn: 0.8907376	total: 2.46s	remaining: 157ms
94:	learn: 0.8907376	total: 2.47s	remaining: 130ms
95:	learn: 0.8907376	total: 2.48s	remaining: 104ms
96:	learn: 0.8907376	total: 2.5s	remaining: 77.5ms
97:	learn: 0.8907376	total: 2.52s	remaining: 51.4ms
98:	learn: 0.8907376	total: 2.54s	remaining: 25.6ms
99:	learn: 0.8907376	total: 2.57s	remaining: 0us
0:	learn: 0.8855247	total: 18.8m

48:	learn: 0.8882615	total: 1.13s	remaining: 1.18s
49:	learn: 0.8882806	total: 1.15s	remaining: 1.15s
50:	learn: 0.8882806	total: 1.16s	remaining: 1.12s
51:	learn: 0.8882806	total: 1.18s	remaining: 1.08s
52:	learn: 0.8882806	total: 1.19s	remaining: 1.06s
53:	learn: 0.8882806	total: 1.2s	remaining: 1.02s
54:	learn: 0.8882806	total: 1.22s	remaining: 995ms
55:	learn: 0.8882806	total: 1.23s	remaining: 965ms
56:	learn: 0.8882806	total: 1.24s	remaining: 939ms
57:	learn: 0.8882806	total: 1.25s	remaining: 909ms
58:	learn: 0.8882806	total: 1.27s	remaining: 884ms
59:	learn: 0.8882615	total: 1.29s	remaining: 863ms
60:	learn: 0.8882615	total: 1.31s	remaining: 838ms


KeyboardInterrupt: 

In [ ]:
# Build new classifier with best hyperparameters. Train model on full dataset

# Generate pseudo-labels for unlabeled data using the model
pseudo_labels = cb['model'].predict(X_unlabeled)


# Combine labeled and unlabeled data with their respective pseudo-labels
X_combined = np.concatenate((training_data_final2, X_unlabeled), axis=0)
y_combined = np.concatenate((training_labels_new, pseudo_labels), axis=0)

### take best hyperparameters from above and retrain model ###

CatBoost_final = CatBoostClassifier(iterations=200,random_seed=random_state,class_weights= [1, 1], 
                              custom_loss= 'Recall', depth= 10, eval_metric= 'Recall', l2_leaf_reg= 4,
                              learning_rate= 0.1, random_strength= 0)


CatBoost_final.fit(
    X_combined, y_combined,
    cat_features=categorical_features_indices,
    eval_set=(X_test, y_test),
    )


In [ ]:
test_model(CatBoost_final, X_combined, y_combined, X_test, y_test)

final_predictions = CatBoost_final.predict(X_combined)
total = len(final_predictions)
calc = np.sum(final_predictions==1)
print('TS predicted: ',calc)
print('percentage: ',calc/total)

In [ ]:
print(CatBoost_final.get_feature_importance(prettified=True))

print(catboost_columns)

### 4. write out predictions to csv

In [ ]:
# write out predictions to csv

output_columns = ['Linkedin_url','Summary', 'Skills', 'title_1',
           'company_1', 'time_duration_1', 'Job_Description_1',
           'First Name','Middle Name', 'Surname', 'City', 'State', 'Country']

# Combine labeled and unlabeled data with their respective pseudo-labels
X_out = np.concatenate((training_data_new[output_columns], X_unlabeled_raw[output_columns]), axis=0)
y_out = np.concatenate((training_labels_new, pseudo_labels), axis=0)

pred_ts = CatBoost_final.predict(X_combined)
pred_proba = CatBoost_final.predict_proba(X_combined)

X_out = pd.DataFrame(X_out, columns=output_columns)



output = X_out[pred_ts == 1]
proba_df = pd.DataFrame(pred_proba)
output_proba = proba_df.loc[pred_ts == 1, 1]
output['confidence'] = output_proba

#output = output[output_columns]
filename_out = 'predictions/final__predictions.csv'
output.to_csv(filename_out, index=False)



In [ ]:
### Analyze output ###

freq = output['company_1'].value_counts()/len(training_df)
print(freq[:30])
print(len(output))